# Data Transformation Courselet

**Authors:**
 - David Koop (dakoop@niu.edu)

**Last Updated:** 2025-10-06

This courselet provides information on using polars to do data transformation. Data transformation is the process of converting data from one format or structure to another, in order to prepare it for analysis or to make it more useful for a specific application or use case. It is an important step in the data preparation process before analysis or modeling is performed. While analysis may be possible without transformation, it often leads to cumbersome and difficult queries. The concept of "tidy data" is to ensure a standard structure that allows standard queries.

This courselet also uses two versions of the climate data from the [National Centers for Environmental Information](https://www.ncei.noaa.gov) which is part of the [National Oceanic and Atmospheric Administration](https://www.noaa.gov). We modified one of the datasets to demonstrate different types of transformations. Both of the datasets are available [here](https://github.com/dakoop/fount-data-transformation/). The original dly dataset is [MXN00017004.dly](https://www1.ncdc.noaa.gov/pub/data/ghcn/daily/all/MXN00017004.dly) and the hierarchical data is constructed from the MXN00017001-MXN00017008 csv files [here](https://www.ncei.noaa.gov/data/global-historical-climatology-network-daily/access/).

In [1]:
import urllib.request
from pathlib import Path

fname = Path("weather.dly")
url = "https://raw.githubusercontent.com/dakoop/fount-data-transformation/refs/heads/main/weather.dly"
if not fname.exists():
    urllib.request.urlretrieve(url, fname)

## Loading and Cleaning Data

We will be reading dly format data from the NCEI. This format is a fixed-width format, where each line of the file is broken into fields based on specified character ranges. The format is documented, and we can use regular expressions to extract these groups from the file. Finally, we convert all integer from strings.

In [2]:
# ghcn dly file format detailed here:
# https://www1.ncdc.noaa.gov/pub/data/ghcn/daily/readme.txt

# ------------------------------
# Variable   Columns   Type
# ------------------------------
# ID            1-11   Character
# YEAR         12-15   Integer
# MONTH        16-17   Integer
# ELEMENT      18-21   Character
# VALUE1       22-26   Integer
# MFLAG1       27-27   Character
# QFLAG1       28-28   Character
# SFLAG1       29-29   Character
# VALUE2       30-34   Integer
# MFLAG2       35-35   Character
# QFLAG2       36-36   Character
# SFLAG2       37-37   Character
#   .           .          .
#   .           .          .
#   .           .          .
# VALUE31    262-266   Integer
# MFLAG31    267-267   Character
# QFLAG31    268-268   Character
# SFLAG31    269-269   Character
# ------------------------------

# parsing using extract_groups
# h/t https://stackoverflow.com/a/78545671

import polars as pl

# Read file as a single-column DataFrame
wdf = pl.read_csv(
    "weather.dly",
    separator="\n",
    has_header=False,
    new_columns=["data"],
)

# Extract columns with regex
days = "".join(
    [
        f"(?<value{d}>.{{5}})(?<mflag{d}>.{{1}})(?<qflag{d}>.{{1}})(?<sflag{d}>.{{1}})"
        for d in range(1, 32)
    ]
)
wdf = wdf.select(
    pl.col("data").str.extract_groups(
        r"^(?<id>.{11})(?<year>.{4})(?<month>.{2})(?<element>.{4})" + days + "$"
    )
).unnest("data")

wdf = wdf.with_columns(
    pl.col("year", "month", r"^value\d*$").str.strip_chars().cast(pl.Int32),
    pl.col("element").str.to_lowercase(),
)

shape: (2_065, 128)
┌─────────────┬──────┬───────┬─────────┬───┬─────────┬─────────┬─────────┬─────────┐
│ id          ┆ year ┆ month ┆ element ┆ … ┆ value31 ┆ mflag31 ┆ qflag31 ┆ sflag31 │
│ ---         ┆ ---  ┆ ---   ┆ ---     ┆   ┆ ---     ┆ ---     ┆ ---     ┆ ---     │
│ str         ┆ i32  ┆ i32   ┆ str     ┆   ┆ i32     ┆ str     ┆ str     ┆ str     │
╞═════════════╪══════╪═══════╪═════════╪═══╪═════════╪═════════╪═════════╪═════════╡
│ MXN00017004 ┆ 1955 ┆ 4     ┆ tmax    ┆ … ┆ -9999   ┆         ┆         ┆         │
│ MXN00017004 ┆ 1955 ┆ 4     ┆ tmin    ┆ … ┆ -9999   ┆         ┆         ┆         │
│ MXN00017004 ┆ 1955 ┆ 4     ┆ prcp    ┆ … ┆ -9999   ┆         ┆         ┆         │
│ MXN00017004 ┆ 1955 ┆ 5     ┆ tmax    ┆ … ┆ 289     ┆         ┆         ┆ m       │
│ MXN00017004 ┆ 1955 ┆ 5     ┆ tmin    ┆ … ┆ 156     ┆         ┆         ┆ m       │
│ …           ┆ …    ┆ …     ┆ …       ┆ … ┆ …       ┆ …       ┆ …       ┆ …       │
│ MXN00017004 ┆ 2013 ┆ 4     ┆ tmin    ┆ … ┆ -9999   ┆         ┆         ┆         │
│ MXN00017004 ┆ 2013 ┆ 4     ┆ prcp    ┆ … ┆ -9999   ┆         ┆         ┆         │
│ MXN00017004 ┆ 2013 ┆ 5     ┆ tmax    ┆ … ┆ 289     ┆         ┆         ┆ m       │
│ MXN00017004 ┆ 2013 ┆ 5     ┆ tmin    ┆ … ┆ 156     ┆         ┆         ┆ m       │
│ MXN00017004 ┆ 2013 ┆ 5     ┆ prcp    ┆ … ┆ 3       ┆         ┆         ┆ m       │
└─────────────┴──────┴───────┴─────────┴───┴─────────┴─────────┴─────────┴─────────┘

Next, we have some data cleaning and formatting to do. This format uses -9999 to refer to missing or undefined values like the 31st of the month for months that have fewer than 31 days. We can set these to null. We can also divide each value by 10 since they are specified in tenths. Finally, while the m and q-flags contain information, we will ignore them and set each valueN field to dN instead.

In [3]:
wdf = (
    wdf.with_columns(pl.col(r"^value\d*$").replace(-9999, None) / 10).select(
        pl.col("id", "year", "month", "element", r"^value.*$")
    )
).rename(lambda c: f"d{c[5:]}" if c.startswith("value") else c)

shape: (2_065, 35)
┌─────────────┬──────┬───────┬─────────┬───┬──────┬──────┬──────┬──────┐
│ id          ┆ year ┆ month ┆ element ┆ … ┆ d28  ┆ d29  ┆ d30  ┆ d31  │
│ ---         ┆ ---  ┆ ---   ┆ ---     ┆   ┆ ---  ┆ ---  ┆ ---  ┆ ---  │
│ str         ┆ i32  ┆ i32   ┆ str     ┆   ┆ f64  ┆ f64  ┆ f64  ┆ f64  │
╞═════════════╪══════╪═══════╪═════════╪═══╪══════╪══════╪══════╪══════╡
│ MXN00017004 ┆ 1955 ┆ 4     ┆ tmax    ┆ … ┆ 33.9 ┆ 32.8 ┆ 31.7 ┆ null │
│ MXN00017004 ┆ 1955 ┆ 4     ┆ tmin    ┆ … ┆ 16.7 ┆ 17.8 ┆ 15.6 ┆ null │
│ MXN00017004 ┆ 1955 ┆ 4     ┆ prcp    ┆ … ┆ 0.0  ┆ 0.0  ┆ 0.5  ┆ null │
│ MXN00017004 ┆ 1955 ┆ 5     ┆ tmax    ┆ … ┆ 31.7 ┆ 30.6 ┆ 30.0 ┆ 28.9 │
│ MXN00017004 ┆ 1955 ┆ 5     ┆ tmin    ┆ … ┆ 15.0 ┆ 16.7 ┆ 15.0 ┆ 15.6 │
│ …           ┆ …    ┆ …     ┆ …       ┆ … ┆ …    ┆ …    ┆ …    ┆ …    │
│ MXN00017004 ┆ 2013 ┆ 4     ┆ tmin    ┆ … ┆ 16.1 ┆ 15.6 ┆ 15.6 ┆ null │
│ MXN00017004 ┆ 2013 ┆ 4     ┆ prcp    ┆ … ┆ 0.0  ┆ 0.0  ┆ 0.0  ┆ null │
│ MXN00017004 ┆ 2013 ┆ 5     ┆ tmax    ┆ … ┆ 29.4 ┆ 26.1 ┆ 26.7 ┆ 28.9 │
│ MXN00017004 ┆ 2013 ┆ 5     ┆ tmin    ┆ … ┆ 15.0 ┆ 15.0 ┆ 15.0 ┆ 15.6 │
│ MXN00017004 ┆ 2013 ┆ 5     ┆ prcp    ┆ … ┆ 24.1 ┆ 1.3  ┆ 0.0  ┆ 0.3  │
└─────────────┴──────┴───────┴─────────┴───┴──────┴──────┴──────┴──────┘

## Tidy Data

There are a few problems with this dataset. In his paper, [Tidy Data](https://vita.had.co.nz/papers/tidy-data.pdf), Hadley Wickham defines tidy data as data where:

 1. Each variable forms a column .
 2. Each observation forms a row.
 3. Each type of observational unit forms a table.

From this, he identifies a number of problems with data (data that is **messy** or **untidy**):
 
 - Column headers are values, not variable names.
 - Multiple variables are stored in one column.
 - Variables are stored in both rows and columns.
 - Multiple types of observational units are stored in the same table.
 - A single observational unit is stored in multiple tables.

In our dataset (identified by Wickham), we have this day variable encoded in the column headers (d1, d2, ...), and we have multiple variables in each column (tmin, tmax, and prcp values are all stored in each of the dN columns).

To fix this, we need to move the values from the columns to the rows, and separate the values in the same column so that they appear in different columns. The first type of operation is an **unpivot**, but it is also referred to as pivot_longer or melting. The second type of operation is its inverse, a **pivot**, sometimes referred to as pivot_wider.

### Unpivot

To unpivot, we need to identify the columns that will become values and those columns we wish to preserve. Polars will take any values in these columns and move them to the correct row. In our case, we choose to identify the non-day columns (the `index` argument) and polars uses the rest as those to unpivot (the `on` argument).

In [4]:
wdf_up = wdf.unpivot(index=["id", "year", "month", "element"])

shape: (64_015, 6)
┌─────────────┬──────┬───────┬─────────┬──────────┬───────┐
│ id          ┆ year ┆ month ┆ element ┆ variable ┆ value │
│ ---         ┆ ---  ┆ ---   ┆ ---     ┆ ---      ┆ ---   │
│ str         ┆ i32  ┆ i32   ┆ str     ┆ str      ┆ f64   │
╞═════════════╪══════╪═══════╪═════════╪══════════╪═══════╡
│ MXN00017004 ┆ 1955 ┆ 4     ┆ tmax    ┆ d1       ┆ 30.6  │
│ MXN00017004 ┆ 1955 ┆ 4     ┆ tmin    ┆ d1       ┆ 15.0  │
│ MXN00017004 ┆ 1955 ┆ 4     ┆ prcp    ┆ d1       ┆ 0.0   │
│ MXN00017004 ┆ 1955 ┆ 5     ┆ tmax    ┆ d1       ┆ 30.6  │
│ MXN00017004 ┆ 1955 ┆ 5     ┆ tmin    ┆ d1       ┆ 20.0  │
│ …           ┆ …    ┆ …     ┆ …       ┆ …        ┆ …     │
│ MXN00017004 ┆ 2013 ┆ 4     ┆ tmin    ┆ d31      ┆ null  │
│ MXN00017004 ┆ 2013 ┆ 4     ┆ prcp    ┆ d31      ┆ null  │
│ MXN00017004 ┆ 2013 ┆ 5     ┆ tmax    ┆ d31      ┆ 28.9  │
│ MXN00017004 ┆ 2013 ┆ 5     ┆ tmin    ┆ d31      ┆ 15.6  │
│ MXN00017004 ┆ 2013 ┆ 5     ┆ prcp    ┆ d31      ┆ 0.3   │
└─────────────┴──────┴───────┴─────────┴──────────┴───────┘

We have a few issues here that we could clear up. First, the name of the new column for the dN values is just "variable" and the name for the values is the generic "value". Since we have a mix of temperatures and precipitation, we'll keep the value name, but let's change "variable" to "day". We can do this when unpivoting via the `variable_name` argument; the `value_name` works similarly.

Second, we have null values in our value column. For now, we will log this and come back to it later.

In [5]:
wdf_up = wdf.unpivot(index=["id", "year", "month", "element"], variable_name="day")

shape: (64_015, 6)
┌─────────────┬──────┬───────┬─────────┬─────┬───────┐
│ id          ┆ year ┆ month ┆ element ┆ day ┆ value │
│ ---         ┆ ---  ┆ ---   ┆ ---     ┆ --- ┆ ---   │
│ str         ┆ i32  ┆ i32   ┆ str     ┆ str ┆ f64   │
╞═════════════╪══════╪═══════╪═════════╪═════╪═══════╡
│ MXN00017004 ┆ 1955 ┆ 4     ┆ tmax    ┆ d1  ┆ 30.6  │
│ MXN00017004 ┆ 1955 ┆ 4     ┆ tmin    ┆ d1  ┆ 15.0  │
│ MXN00017004 ┆ 1955 ┆ 4     ┆ prcp    ┆ d1  ┆ 0.0   │
│ MXN00017004 ┆ 1955 ┆ 5     ┆ tmax    ┆ d1  ┆ 30.6  │
│ MXN00017004 ┆ 1955 ┆ 5     ┆ tmin    ┆ d1  ┆ 20.0  │
│ …           ┆ …    ┆ …     ┆ …       ┆ …   ┆ …     │
│ MXN00017004 ┆ 2013 ┆ 4     ┆ tmin    ┆ d31 ┆ null  │
│ MXN00017004 ┆ 2013 ┆ 4     ┆ prcp    ┆ d31 ┆ null  │
│ MXN00017004 ┆ 2013 ┆ 5     ┆ tmax    ┆ d31 ┆ 28.9  │
│ MXN00017004 ┆ 2013 ┆ 5     ┆ tmin    ┆ d31 ┆ 15.6  │
│ MXN00017004 ┆ 2013 ┆ 5     ┆ prcp    ┆ d31 ┆ 0.3   │
└─────────────┴──────┴───────┴─────────┴─────┴───────┘

##### Exercise

Combine the year, month, and date columns into a single date column.

##### Solution

In [41]:
wdf_date = wdf_up.with_columns(
    pl.col("day").str.replace("d", "").cast(pl.Int32)
).with_columns(pl.date(pl.col("year"), pl.col("month"), pl.col("day")).alias("date"))

shape: (64_015, 7)
┌─────────────┬──────┬───────┬─────────┬─────┬───────┬────────────┐
│ id          ┆ year ┆ month ┆ element ┆ day ┆ value ┆ date       │
│ ---         ┆ ---  ┆ ---   ┆ ---     ┆ --- ┆ ---   ┆ ---        │
│ str         ┆ i32  ┆ i32   ┆ str     ┆ i32 ┆ f64   ┆ date       │
╞═════════════╪══════╪═══════╪═════════╪═════╪═══════╪════════════╡
│ MXN00017004 ┆ 1955 ┆ 4     ┆ tmax    ┆ 1   ┆ 30.6  ┆ 1955-04-01 │
│ MXN00017004 ┆ 1955 ┆ 4     ┆ tmin    ┆ 1   ┆ 15.0  ┆ 1955-04-01 │
│ MXN00017004 ┆ 1955 ┆ 4     ┆ prcp    ┆ 1   ┆ 0.0   ┆ 1955-04-01 │
│ MXN00017004 ┆ 1955 ┆ 5     ┆ tmax    ┆ 1   ┆ 30.6  ┆ 1955-05-01 │
│ MXN00017004 ┆ 1955 ┆ 5     ┆ tmin    ┆ 1   ┆ 20.0  ┆ 1955-05-01 │
│ …           ┆ …    ┆ …     ┆ …       ┆ …   ┆ …     ┆ …          │
│ MXN00017004 ┆ 2013 ┆ 4     ┆ tmin    ┆ 31  ┆ null  ┆ null       │
│ MXN00017004 ┆ 2013 ┆ 4     ┆ prcp    ┆ 31  ┆ null  ┆ null       │
│ MXN00017004 ┆ 2013 ┆ 5     ┆ tmax    ┆ 31  ┆ 28.9  ┆ 2013-05-31 │
│ MXN00017004 ┆ 2013 ┆ 5     ┆ tmin    ┆ 31  ┆ 15.6  ┆ 2013-05-31 │
│ MXN00017004 ┆ 2013 ┆ 5     ┆ prcp    ┆ 31  ┆ 0.3   ┆ 2013-05-31 │
└─────────────┴──────┴───────┴─────────┴─────┴───────┴────────────┘

Note that there are null dates here. Whenever the day is invalid (e.g., 2013-04-31), polars will not be able to construct a date. We can drop these rows which should also drop many of our null values.

In [7]:
wdf_date = wdf_date.drop_nulls("date").drop("year", "month", "day")

shape: (62_851, 4)
┌─────────────┬─────────┬───────┬────────────┐
│ id          ┆ element ┆ value ┆ date       │
│ ---         ┆ ---     ┆ ---   ┆ ---        │
│ str         ┆ str     ┆ f64   ┆ date       │
╞═════════════╪═════════╪═══════╪════════════╡
│ MXN00017004 ┆ tmax    ┆ 30.6  ┆ 1955-04-01 │
│ MXN00017004 ┆ tmin    ┆ 15.0  ┆ 1955-04-01 │
│ MXN00017004 ┆ prcp    ┆ 0.0   ┆ 1955-04-01 │
│ MXN00017004 ┆ tmax    ┆ 30.6  ┆ 1955-05-01 │
│ MXN00017004 ┆ tmin    ┆ 20.0  ┆ 1955-05-01 │
│ …           ┆ …       ┆ …     ┆ …          │
│ MXN00017004 ┆ tmin    ┆ 17.8  ┆ 2013-03-31 │
│ MXN00017004 ┆ prcp    ┆ 0.0   ┆ 2013-03-31 │
│ MXN00017004 ┆ tmax    ┆ 28.9  ┆ 2013-05-31 │
│ MXN00017004 ┆ tmin    ┆ 15.6  ┆ 2013-05-31 │
│ MXN00017004 ┆ prcp    ┆ 0.3   ┆ 2013-05-31 │
└─────────────┴─────────┴───────┴────────────┘

### Pivot

Now, we need to move the values in the `element` column into new columns. Each unique value in that column becomes a new column itself. With pivot, we need to identify the `values` column and the column of new column names (`on`). The remainder (the `index`) will stay as is. You can see why we didn't need to bother to retitle the value column.

In [8]:
wdf_tidy = wdf_date.pivot(on="element", values="value").sort("date")

shape: (20_971, 5)
┌─────────────┬────────────┬──────┬──────┬──────┐
│ id          ┆ date       ┆ tmax ┆ tmin ┆ prcp │
│ ---         ┆ ---        ┆ ---  ┆ ---  ┆ ---  │
│ str         ┆ date       ┆ f64  ┆ f64  ┆ f64  │
╞═════════════╪════════════╪══════╪══════╪══════╡
│ MXN00017004 ┆ 1955-04-01 ┆ 30.6 ┆ 15.0 ┆ 0.0  │
│ MXN00017004 ┆ 1955-04-02 ┆ 30.6 ┆ 15.0 ┆ 0.0  │
│ MXN00017004 ┆ 1955-04-03 ┆ 30.6 ┆ 15.6 ┆ 0.0  │
│ MXN00017004 ┆ 1955-04-04 ┆ 31.7 ┆ 15.0 ┆ 0.0  │
│ MXN00017004 ┆ 1955-04-05 ┆ 32.8 ┆ 15.6 ┆ 0.0  │
│ …           ┆ …          ┆ …    ┆ …    ┆ …    │
│ MXN00017004 ┆ 2013-05-27 ┆ 27.2 ┆ 14.4 ┆ 21.3 │
│ MXN00017004 ┆ 2013-05-28 ┆ 29.4 ┆ 15.0 ┆ 24.1 │
│ MXN00017004 ┆ 2013-05-29 ┆ 26.1 ┆ 15.0 ┆ 1.3  │
│ MXN00017004 ┆ 2013-05-30 ┆ 26.7 ┆ 15.0 ┆ 0.0  │
│ MXN00017004 ┆ 2013-05-31 ┆ 28.9 ┆ 15.6 ┆ 0.3  │
└─────────────┴────────────┴──────┴──────┴──────┘

This dataset is now tidy. We can ask for the minimum temperature, maximum temperature, and precipitation, for any date. We can also determine the absolute maximum or minimum temperatures, or the most precepitation in a day.

### Transpose

While tidy data is often the most useful for querying datasets, it may not work best for studying the data or displaying it. For example, suppose we wish to show the data for the first ten days of April 2012. We might want to display these dates as different columns as in the original dataset. While we could use a pivot, we can also use a transpose.

In [ ]:
wdf_tidy.drop("id").filter(
    (pl.col("date") <= pl.date(2012, 4, 10)) & (pl.col("date") >= pl.date(2012, 4, 1))
).transpose()

shape: (4, 10)
┌──────────┬──────────┬──────────┬──────────┬───┬──────────┬──────────┬──────────┬──────────┐
│ column_0 ┆ column_1 ┆ column_2 ┆ column_3 ┆ … ┆ column_6 ┆ column_7 ┆ column_8 ┆ column_9 │
│ ---      ┆ ---      ┆ ---      ┆ ---      ┆   ┆ ---      ┆ ---      ┆ ---      ┆ ---      │
│ f64      ┆ f64      ┆ f64      ┆ f64      ┆   ┆ f64      ┆ f64      ┆ f64      ┆ f64      │
╞══════════╪══════════╪══════════╪══════════╪═══╪══════════╪══════════╪══════════╪══════════╡
│ 15431.0  ┆ 15432.0  ┆ 15433.0  ┆ 15434.0  ┆ … ┆ 15437.0  ┆ 15438.0  ┆ 15439.0  ┆ 15440.0  │
│ 31.7     ┆ 31.7     ┆ 33.9     ┆ 35.0     ┆ … ┆ 35.0     ┆ 35.0     ┆ 35.6     ┆ 31.7     │
│ 15.0     ┆ 13.9     ┆ 13.9     ┆ 13.9     ┆ … ┆ 15.6     ┆ 15.6     ┆ 15.6     ┆ 15.6     │
│ 0.0      ┆ 0.0      ┆ 0.0      ┆ 0.0      ┆ … ┆ 0.0      ┆ 0.0      ┆ 0.0      ┆ 0.0      │
└──────────┴──────────┴──────────┴──────────┴───┴──────────┴──────────┴──────────┴──────────┘

Hmm, we have lost some information here, and our dates have become floats. We no longer know which rows are temperature or precipitation, and the columns are unhelpfully named `column_N`. The dates are floats because the types of the columns must agree so polars transformed the dates to floating point values. Let's use the `include_header`, `header_name`, and `column_names` arguments to fix this.

In [10]:
wdf_tidy.drop("id").filter(
    (pl.col("date") <= pl.date(2012, 4, 10)) & (pl.col("date") >= pl.date(2012, 4, 1))
).transpose(include_header=True, header_name="measure", column_names="date")

SchemaError: invalid series dtype: expected `String`, got `date`

polars needs the column names to be strings and we are passing dates so we must cast these first.

In [11]:
wdf_2012_04 = (
    wdf_tidy.drop("id")
    .filter(
        (pl.col("date") <= pl.date(2012, 4, 10))
        & (pl.col("date") >= pl.date(2012, 4, 1))
    )
    .with_columns(pl.col("date").cast(pl.String))
    .transpose(include_header=True, header_name="measure", column_names="date")
)

shape: (3, 11)
┌─────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ measure ┆ 2012-04-01 ┆ 2012-04-0 ┆ 2012-04-0 ┆ … ┆ 2012-04-0 ┆ 2012-04-0 ┆ 2012-04-0 ┆ 2012-04-1 │
│ ---     ┆ ---        ┆ 2         ┆ 3         ┆   ┆ 7         ┆ 8         ┆ 9         ┆ 0         │
│ str     ┆ f64        ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---       │
│         ┆            ┆ f64       ┆ f64       ┆   ┆ f64       ┆ f64       ┆ f64       ┆ f64       │
╞═════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ tmax    ┆ 31.7       ┆ 31.7      ┆ 33.9      ┆ … ┆ 35.0      ┆ 35.0      ┆ 35.6      ┆ 31.7      │
│ tmin    ┆ 15.0       ┆ 13.9      ┆ 13.9      ┆ … ┆ 15.6      ┆ 15.6      ┆ 15.6      ┆ 15.6      │
│ prcp    ┆ 0.0        ┆ 0.0       ┆ 0.0       ┆ … ┆ 0.0       ┆ 0.0       ┆ 0.0       ┆ 0.0       │
└─────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

### Concatenation

We might wish to compare these values to the same values from 2013. We can obtain the 2013 values the same way as we did for 2012.

In [12]:
wdf_2013_04 = (
    wdf_tidy.drop("id")
    .filter(
        (pl.col("date") <= pl.date(2013, 4, 10))
        & (pl.col("date") >= pl.date(2013, 4, 1))
    )
    .with_columns(pl.col("date").cast(pl.String))
    .transpose(include_header=True, header_name="measure", column_names="date")
)

shape: (3, 11)
┌─────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ measure ┆ 2013-04-01 ┆ 2013-04-0 ┆ 2013-04-0 ┆ … ┆ 2013-04-0 ┆ 2013-04-0 ┆ 2013-04-0 ┆ 2013-04-1 │
│ ---     ┆ ---        ┆ 2         ┆ 3         ┆   ┆ 7         ┆ 8         ┆ 9         ┆ 0         │
│ str     ┆ f64        ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---       │
│         ┆            ┆ f64       ┆ f64       ┆   ┆ f64       ┆ f64       ┆ f64       ┆ f64       │
╞═════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ tmax    ┆ 35.0       ┆ 35.0      ┆ 35.0      ┆ … ┆ 33.9      ┆ 31.1      ┆ 30.6      ┆ 32.2      │
│ tmin    ┆ 20.0       ┆ 18.9      ┆ 17.8      ┆ … ┆ 16.1      ┆ 17.8      ┆ 16.7      ┆ 16.1      │
│ prcp    ┆ 0.0        ┆ 0.0       ┆ 0.0       ┆ … ┆ 0.0       ┆ 0.0       ┆ 0.0       ┆ 0.0       │
└─────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

If we want to put these into one table, we need to stack these on top of each other.

In [13]:
pl.concat([wdf_2012_04, wdf_2013_04])

ShapeError: unable to vstack, column names don't match: "2012-04-01" and "2013-04-01"

Unfortunately, the column names don't match so this relational union is not allowed. We can try other strategies like "diagonal" or "align", but neither of these does what we want.

In [14]:
pl.concat([wdf_2012_04, wdf_2013_04], how="diagonal")

shape: (6, 21)
┌─────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ measure ┆ 2012-04-01 ┆ 2012-04-0 ┆ 2012-04-0 ┆ … ┆ 2013-04-0 ┆ 2013-04-0 ┆ 2013-04-0 ┆ 2013-04-1 │
│ ---     ┆ ---        ┆ 2         ┆ 3         ┆   ┆ 7         ┆ 8         ┆ 9         ┆ 0         │
│ str     ┆ f64        ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---       │
│         ┆            ┆ f64       ┆ f64       ┆   ┆ f64       ┆ f64       ┆ f64       ┆ f64       │
╞═════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ tmax    ┆ 31.7       ┆ 31.7      ┆ 33.9      ┆ … ┆ null      ┆ null      ┆ null      ┆ null      │
│ tmin    ┆ 15.0       ┆ 13.9      ┆ 13.9      ┆ … ┆ null      ┆ null      ┆ null      ┆ null      │
│ prcp    ┆ 0.0        ┆ 0.0       ┆ 0.0       ┆ … ┆ null      ┆ null      ┆ null      ┆ null      │
│ tmax    ┆ null       ┆ null      ┆ null      ┆ … ┆ 33.9      ┆ 31.1      ┆ 30.6      ┆ 32.2      │
│ tmin    ┆ null       ┆ null      ┆ null      ┆ … ┆ 16.1      ┆ 17.8      ┆ 16.7      ┆ 16.1      │
│ prcp    ┆ null       ┆ null      ┆ null      ┆ … ┆ 0.0       ┆ 0.0       ┆ 0.0       ┆ 0.0       │
└─────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

In [15]:
pl.concat([wdf_2012_04, wdf_2013_04], how="align")

shape: (3, 21)
┌─────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ measure ┆ 2012-04-01 ┆ 2012-04-0 ┆ 2012-04-0 ┆ … ┆ 2013-04-0 ┆ 2013-04-0 ┆ 2013-04-0 ┆ 2013-04-1 │
│ ---     ┆ ---        ┆ 2         ┆ 3         ┆   ┆ 7         ┆ 8         ┆ 9         ┆ 0         │
│ str     ┆ f64        ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---       │
│         ┆            ┆ f64       ┆ f64       ┆   ┆ f64       ┆ f64       ┆ f64       ┆ f64       │
╞═════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ prcp    ┆ 0.0        ┆ 0.0       ┆ 0.0       ┆ … ┆ 0.0       ┆ 0.0       ┆ 0.0       ┆ 0.0       │
│ tmax    ┆ 31.7       ┆ 31.7      ┆ 33.9      ┆ … ┆ 33.9      ┆ 31.1      ┆ 30.6      ┆ 32.2      │
│ tmin    ┆ 15.0       ┆ 13.9      ┆ 13.9      ┆ … ┆ 16.1      ┆ 17.8      ┆ 16.7      ┆ 16.1      │
└─────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

##### Exercise

Rename the date columns so that they will align and then concatenate them. Also make sure to rename the measure values to indicate their year.

##### Solution

In [16]:
pl.concat(
    [
        wdf_2012_04.rename(lambda c: c[5:]).with_columns(
            ("2012 " + pl.col("re")).alias("re")
        ),
        wdf_2013_04.rename(lambda c: c[5:]).with_columns(
            ("2013 " + pl.col("re")).alias("re")
        ),
    ]
).rename({"re": "measure"}).sort(pl.col("measure").str.slice(4))

shape: (6, 11)
┌───────────┬───────┬───────┬───────┬───┬───────┬───────┬───────┬───────┐
│ measure   ┆ 04-01 ┆ 04-02 ┆ 04-03 ┆ … ┆ 04-07 ┆ 04-08 ┆ 04-09 ┆ 04-10 │
│ ---       ┆ ---   ┆ ---   ┆ ---   ┆   ┆ ---   ┆ ---   ┆ ---   ┆ ---   │
│ str       ┆ f64   ┆ f64   ┆ f64   ┆   ┆ f64   ┆ f64   ┆ f64   ┆ f64   │
╞═══════════╪═══════╪═══════╪═══════╪═══╪═══════╪═══════╪═══════╪═══════╡
│ 2012 prcp ┆ 0.0   ┆ 0.0   ┆ 0.0   ┆ … ┆ 0.0   ┆ 0.0   ┆ 0.0   ┆ 0.0   │
│ 2013 prcp ┆ 0.0   ┆ 0.0   ┆ 0.0   ┆ … ┆ 0.0   ┆ 0.0   ┆ 0.0   ┆ 0.0   │
│ 2012 tmax ┆ 31.7  ┆ 31.7  ┆ 33.9  ┆ … ┆ 35.0  ┆ 35.0  ┆ 35.6  ┆ 31.7  │
│ 2013 tmax ┆ 35.0  ┆ 35.0  ┆ 35.0  ┆ … ┆ 33.9  ┆ 31.1  ┆ 30.6  ┆ 32.2  │
│ 2012 tmin ┆ 15.0  ┆ 13.9  ┆ 13.9  ┆ … ┆ 15.6  ┆ 15.6  ┆ 15.6  ┆ 15.6  │
│ 2013 tmin ┆ 20.0  ┆ 18.9  ┆ 17.8  ┆ … ┆ 16.1  ┆ 17.8  ┆ 16.7  ┆ 16.1  │
└───────────┴───────┴───────┴───────┴───┴───────┴───────┴───────┴───────┘

## Hierarchical Data

For the next topic, we will use a restructured version of similar data from NCEI. This structure mirrors real-world hierarchical data. We can load JSON data using Python's standard library or via polars directly. Loading the data with the standard library allows us to explore the structures using Python's dictionaries and lists.

In [17]:
import urllib.request
from pathlib import Path

fname = Path("weather.json")
url = "https://raw.githubusercontent.com/dakoop/fount-data-transformation/refs/heads/main/weather.json"
if not fname.exists():
    urllib.request.urlretrieve(url, fname)

In [18]:
import json

d = json.load(open("weather.json"))
d[:2]

[{'STATION': {'ID': 'MXN00017004',
   'LATITUDE': 18.9167,
   'LONGITUDE': -99.2333,
   'ELEVATION': 1510.0,
   'NAME': 'CUERNAVACA DGE, MX'},
  'YEAR': 2000,
  'MONTH': 2,
  'PRCP': '0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0',
  'TMIN': '128, 117, 128, 117, 117, 117, 128, 100, 89, 117, 128, 139, 128, 139, 150, 139, 150, 139, 150, 139, 117, 139, 150, 150, 150, 150, 156, 128, 139',
  'TMAX': '267, 267, 256, 250, 250, 256, 256, 239, 256, 278, 289, 278, 289, 278, 278, 267, 261, 267, 267, 256, 267, 289, 267, 278, 278, 256, 256, 250, 328'},
 {'STATION': {'ID': 'MXN00017001',
   'LATITUDE': 18.9333,
   'LONGITUDE': -98.9167,
   'ELEVATION': 1599.9,
   'NAME': 'ATLATLAHUACAN, MX'},
  'YEAR': 2009,
  'MONTH': 5,
  'PRCP': '0, 0, 0, 0, 0, 0, 0, 0, 0, 33, 0, 0, 36, 20, 236, 0, 0, 0, 0, 66, 91, 414, 0, 0, 0, 0, 0, 0, 155, 0, 216',
  'TMIN': '156, 156, 156, 156, 117, 128, 167, 128, 106, 117, 156, 178, 178, 150, 156, 156, 150, 156, 150, 150, 156, 150, 150

In [19]:
d[0].keys()

dict_keys(['STATION', 'YEAR', 'MONTH', 'PRCP', 'TMIN', 'TMAX'])

We can see that the station has information nested inside of it, and the PRCP, TMIN, and TMAX columns are strings with comma-separated values. These strings have 28-31 values depending on which month it is, one for each day of the month. We can pass the parsed JSON data to polars' DataFrame constructor, or just have polars load it directly via `read_json`.

In [20]:
df = pl.DataFrame(d)

shape: (741, 6)
┌────────────────────┬──────┬───────┬────────────────────┬────────────────────┬────────────────────┐
│ STATION            ┆ YEAR ┆ MONTH ┆ PRCP               ┆ TMIN               ┆ TMAX               │
│ ---                ┆ ---  ┆ ---   ┆ ---                ┆ ---                ┆ ---                │
│ struct[5]          ┆ i64  ┆ i64   ┆ str                ┆ str                ┆ str                │
╞════════════════════╪══════╪═══════╪════════════════════╪════════════════════╪════════════════════╡
│ {"MXN00017004",18. ┆ 2000 ┆ 2     ┆ 0, 0, 0, 0, 0, 0,  ┆ 128, 117, 128,     ┆ 267, 267, 256,     │
│ 9167,-99.233…      ┆      ┆       ┆ 0, 0, 0, 0, …      ┆ 117, 117, 117, …   ┆ 250, 250, 256, …   │
│ {"MXN00017001",18. ┆ 2009 ┆ 5     ┆ 0, 0, 0, 0, 0, 0,  ┆ 156, 156, 156,     ┆ 306, 306, 300,     │
│ 9333,-98.916…      ┆      ┆       ┆ 0, 0, 0, 33,…      ┆ 156, 117, 128, …   ┆ 317, 317, 317, …   │
│ {"MXN00017006",18. ┆ 2002 ┆ 3     ┆ 0, 0, 0, 0, 0, 0,  ┆ 150, 150, 178,     ┆ 256, 256, 289,     │
│ 7667,-99.316…      ┆      ┆       ┆ 15, 0, 0, 0,…      ┆ 156, 167, 156, …   ┆ 289, 267, 278, …   │
│ {"MXN00017001",18. ┆ 2003 ┆ 5     ┆ 0, 0, 0, 0, 0, 0,  ┆ 139, 128, 117,     ┆ 339, 356, 339,     │
│ 9333,-98.916…      ┆      ┆       ┆ 0, 0, 18, 0,…      ┆ 106, 128, 128, …   ┆ 350, 356, 350, …   │
│ {"MXN00017007",18. ┆ 2001 ┆ 1     ┆ 0, 0, 0, 0, 0, 0,  ┆ 139, 128, 150,     ┆ 300, 300, 289,     │
│ 6,-99.4167,9…      ┆      ┆       ┆ 0, 0, 41, 0,…      ┆ 117, 117, 117, …   ┆ 306, 317, 317, …   │
│ …                  ┆ …    ┆ …     ┆ …                  ┆ …                  ┆ …                  │
│ {"MXN00017003",18. ┆ 2009 ┆ 11    ┆ 28, 30, 0, 0, 0,   ┆ 150, 156, 128,     ┆ 250, 256, 256,     │
│ 8,-98.95,130…      ┆      ┆       ┆ 0, 0, 0, 0, 0…     ┆ 139, 139, 128, …   ┆ 256, 256, 250, …   │
│ {"MXN00017008",18. ┆ 2007 ┆ 11    ┆ 0, 0, 0, 0, 0, 0,  ┆ 139, 128, 106,     ┆ 317, 317, 328,     │
│ 4333,-99.016…      ┆      ┆       ┆ 0, 0, 0, 0, …      ┆ 128, 106, 117, …   ┆ 300, 300, 289, …   │
│ {"MXN00017001",18. ┆ 2008 ┆ 9     ┆ 0, 117, 198, 41,   ┆ 139, 156, 128,     ┆ 239, 217, 250,     │
│ 9333,-98.916…      ┆      ┆       ┆ 193, 20, 211,…     ┆ 156, 150, 139, …   ┆ 217, 228, 228, …   │
│ {"MXN00017001",18. ┆ 2002 ┆ 6     ┆ 99, 79, 249, 0,    ┆ 106, 89, 100, 106, ┆ 300, 306, 317,     │
│ 9333,-98.916…      ┆      ┆       ┆ 99, 0, 0, 0, 0…    ┆ 117, 100, 1…       ┆ 300, 306, 317, …   │
│ {"MXN00017001",18. ┆ 2004 ┆ 4     ┆ 0, 0, 0, 0, 0, 28, ┆ 150, 139, 150,     ┆ 278, 317, 328,     │
│ 9333,-98.916…      ┆      ┆       ┆ 0, 0, 0, 0,…       ┆ 156, 139, 139, …   ┆ 339, 356, 356, …   │
└────────────────────┴──────┴───────┴────────────────────┴────────────────────┴────────────────────┘

or load it directly with polars.

In [21]:
import polars as pl

df = pl.read_json("weather.json")

shape: (741, 6)
┌────────────────────┬──────┬───────┬────────────────────┬────────────────────┬────────────────────┐
│ STATION            ┆ YEAR ┆ MONTH ┆ PRCP               ┆ TMIN               ┆ TMAX               │
│ ---                ┆ ---  ┆ ---   ┆ ---                ┆ ---                ┆ ---                │
│ struct[5]          ┆ i64  ┆ i64   ┆ str                ┆ str                ┆ str                │
╞════════════════════╪══════╪═══════╪════════════════════╪════════════════════╪════════════════════╡
│ {"MXN00017004",18. ┆ 2000 ┆ 2     ┆ 0, 0, 0, 0, 0, 0,  ┆ 128, 117, 128,     ┆ 267, 267, 256,     │
│ 9167,-99.233…      ┆      ┆       ┆ 0, 0, 0, 0, …      ┆ 117, 117, 117, …   ┆ 250, 250, 256, …   │
│ {"MXN00017001",18. ┆ 2009 ┆ 5     ┆ 0, 0, 0, 0, 0, 0,  ┆ 156, 156, 156,     ┆ 306, 306, 300,     │
│ 9333,-98.916…      ┆      ┆       ┆ 0, 0, 0, 33,…      ┆ 156, 117, 128, …   ┆ 317, 317, 317, …   │
│ {"MXN00017006",18. ┆ 2002 ┆ 3     ┆ 0, 0, 0, 0, 0, 0,  ┆ 150, 150, 178,     ┆ 256, 256, 289,     │
│ 7667,-99.316…      ┆      ┆       ┆ 15, 0, 0, 0,…      ┆ 156, 167, 156, …   ┆ 289, 267, 278, …   │
│ {"MXN00017001",18. ┆ 2003 ┆ 5     ┆ 0, 0, 0, 0, 0, 0,  ┆ 139, 128, 117,     ┆ 339, 356, 339,     │
│ 9333,-98.916…      ┆      ┆       ┆ 0, 0, 18, 0,…      ┆ 106, 128, 128, …   ┆ 350, 356, 350, …   │
│ {"MXN00017007",18. ┆ 2001 ┆ 1     ┆ 0, 0, 0, 0, 0, 0,  ┆ 139, 128, 150,     ┆ 300, 300, 289,     │
│ 6,-99.4167,9…      ┆      ┆       ┆ 0, 0, 41, 0,…      ┆ 117, 117, 117, …   ┆ 306, 317, 317, …   │
│ …                  ┆ …    ┆ …     ┆ …                  ┆ …                  ┆ …                  │
│ {"MXN00017003",18. ┆ 2009 ┆ 11    ┆ 28, 30, 0, 0, 0,   ┆ 150, 156, 128,     ┆ 250, 256, 256,     │
│ 8,-98.95,130…      ┆      ┆       ┆ 0, 0, 0, 0, 0…     ┆ 139, 139, 128, …   ┆ 256, 256, 250, …   │
│ {"MXN00017008",18. ┆ 2007 ┆ 11    ┆ 0, 0, 0, 0, 0, 0,  ┆ 139, 128, 106,     ┆ 317, 317, 328,     │
│ 4333,-99.016…      ┆      ┆       ┆ 0, 0, 0, 0, …      ┆ 128, 106, 117, …   ┆ 300, 300, 289, …   │
│ {"MXN00017001",18. ┆ 2008 ┆ 9     ┆ 0, 117, 198, 41,   ┆ 139, 156, 128,     ┆ 239, 217, 250,     │
│ 9333,-98.916…      ┆      ┆       ┆ 193, 20, 211,…     ┆ 156, 150, 139, …   ┆ 217, 228, 228, …   │
│ {"MXN00017001",18. ┆ 2002 ┆ 6     ┆ 99, 79, 249, 0,    ┆ 106, 89, 100, 106, ┆ 300, 306, 317,     │
│ 9333,-98.916…      ┆      ┆       ┆ 99, 0, 0, 0, 0…    ┆ 117, 100, 1…       ┆ 300, 306, 317, …   │
│ {"MXN00017001",18. ┆ 2004 ┆ 4     ┆ 0, 0, 0, 0, 0, 28, ┆ 150, 139, 150,     ┆ 278, 317, 328,     │
│ 9333,-98.916…      ┆      ┆       ┆ 0, 0, 0, 0,…       ┆ 156, 139, 139, …   ┆ 339, 356, 356, …   │
└────────────────────┴──────┴───────┴────────────────────┴────────────────────┴────────────────────┘

At this point, we see that `STATION` is a `struct`. Structs are very similar to python dictionaries and have both key-value pairs. We can find more information about the struct from the `fields` and `schema` properties.

In [22]:
df["STATION"].struct.fields

['ID', 'LATITUDE', 'LONGITUDE', 'ELEVATION', 'NAME']

In [23]:
df["STATION"].struct.schema

Schema([('ID', String),
        ('LATITUDE', Float64),
        ('LONGITUDE', Float64),
        ('ELEVATION', Float64),
        ('NAME', String)])

### Unnest

We can also **unnest** the struct which promotes each key to its own column.

In [24]:
df["STATION"].struct.unnest()

shape: (741, 5)
┌─────────────┬──────────┬───────────┬───────────┬────────────────────┐
│ ID          ┆ LATITUDE ┆ LONGITUDE ┆ ELEVATION ┆ NAME               │
│ ---         ┆ ---      ┆ ---       ┆ ---       ┆ ---                │
│ str         ┆ f64      ┆ f64       ┆ f64       ┆ str                │
╞═════════════╪══════════╪═══════════╪═══════════╪════════════════════╡
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ CUERNAVACA DGE, MX │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ ATLATLAHUACAN, MX  │
│ MXN00017006 ┆ 18.7667  ┆ -99.3167  ┆ 1857.8    ┆ EL RODEO, MX       │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ ATLATLAHUACAN, MX  │
│ MXN00017007 ┆ 18.6     ┆ -99.4167  ┆ 941.8     ┆ HUAJINTLAN, MX     │
│ …           ┆ …        ┆ …         ┆ …         ┆ …                  │
│ MXN00017003 ┆ 18.8     ┆ -98.95    ┆ 1302.7    ┆ CUAUTLA SMN, MX    │
│ MXN00017008 ┆ 18.4333  ┆ -99.0167  ┆ 965.9     ┆ HUAUTLA, MX        │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ ATLATLAHUACAN, MX  │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ ATLATLAHUACAN, MX  │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ ATLATLAHUACAN, MX  │
└─────────────┴──────────┴───────────┴───────────┴────────────────────┘

If we wish to keep this information with the rest of the dataframe, we can call the `unnest` function and pass the column we wish to unnest.

In [25]:
udf = df.unnest("STATION")

shape: (741, 10)
┌────────────┬──────────┬───────────┬───────────┬───┬───────┬────────────┬────────────┬────────────┐
│ ID         ┆ LATITUDE ┆ LONGITUDE ┆ ELEVATION ┆ … ┆ MONTH ┆ PRCP       ┆ TMIN       ┆ TMAX       │
│ ---        ┆ ---      ┆ ---       ┆ ---       ┆   ┆ ---   ┆ ---        ┆ ---        ┆ ---        │
│ str        ┆ f64      ┆ f64       ┆ f64       ┆   ┆ i64   ┆ str        ┆ str        ┆ str        │
╞════════════╪══════════╪═══════════╪═══════════╪═══╪═══════╪════════════╪════════════╪════════════╡
│ MXN0001700 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 2     ┆ 0, 0, 0,   ┆ 128, 117,  ┆ 267, 267,  │
│ 4          ┆          ┆           ┆           ┆   ┆       ┆ 0, 0, 0,   ┆ 128, 117,  ┆ 256, 250,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 0, 0, 0,   ┆ 117, 117,  ┆ 250, 256,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 0, …       ┆ …          ┆ …          │
│ MXN0001700 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 5     ┆ 0, 0, 0,   ┆ 156, 156,  ┆ 306, 306,  │
│ 1          ┆          ┆           ┆           ┆   ┆       ┆ 0, 0, 0,   ┆ 156, 156,  ┆ 300, 317,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 0, 0, 0,   ┆ 117, 128,  ┆ 317, 317,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 33,…       ┆ …          ┆ …          │
│ MXN0001700 ┆ 18.7667  ┆ -99.3167  ┆ 1857.8    ┆ … ┆ 3     ┆ 0, 0, 0,   ┆ 150, 150,  ┆ 256, 256,  │
│ 6          ┆          ┆           ┆           ┆   ┆       ┆ 0, 0, 0,   ┆ 178, 156,  ┆ 289, 289,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 15, 0, 0,  ┆ 167, 156,  ┆ 267, 278,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 0,…        ┆ …          ┆ …          │
│ MXN0001700 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 5     ┆ 0, 0, 0,   ┆ 139, 128,  ┆ 339, 356,  │
│ 1          ┆          ┆           ┆           ┆   ┆       ┆ 0, 0, 0,   ┆ 117, 106,  ┆ 339, 350,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 0, 0, 18,  ┆ 128, 128,  ┆ 356, 350,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 0,…        ┆ …          ┆ …          │
│ MXN0001700 ┆ 18.6     ┆ -99.4167  ┆ 941.8     ┆ … ┆ 1     ┆ 0, 0, 0,   ┆ 139, 128,  ┆ 300, 300,  │
│ 7          ┆          ┆           ┆           ┆   ┆       ┆ 0, 0, 0,   ┆ 150, 117,  ┆ 289, 306,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 0, 0, 41,  ┆ 117, 117,  ┆ 317, 317,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 0,…        ┆ …          ┆ …          │
│ …          ┆ …        ┆ …         ┆ …         ┆ … ┆ …     ┆ …          ┆ …          ┆ …          │
│ MXN0001700 ┆ 18.8     ┆ -98.95    ┆ 1302.7    ┆ … ┆ 11    ┆ 28, 30, 0, ┆ 150, 156,  ┆ 250, 256,  │
│ 3          ┆          ┆           ┆           ┆   ┆       ┆ 0, 0, 0,   ┆ 128, 139,  ┆ 256, 256,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 0, 0, 0,   ┆ 139, 128,  ┆ 256, 250,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 0…         ┆ …          ┆ …          │
│ MXN0001700 ┆ 18.4333  ┆ -99.0167  ┆ 965.9     ┆ … ┆ 11    ┆ 0, 0, 0,   ┆ 139, 128,  ┆ 317, 317,  │
│ 8          ┆          ┆           ┆           ┆   ┆       ┆ 0, 0, 0,   ┆ 106, 128,  ┆ 328, 300,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 0, 0, 0,   ┆ 106, 117,  ┆ 300, 289,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 0, …       ┆ …          ┆ …          │
│ MXN0001700 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 9     ┆ 0, 117,    ┆ 139, 156,  ┆ 239, 217,  │
│ 1          ┆          ┆           ┆           ┆   ┆       ┆ 198, 41,   ┆ 128, 156,  ┆ 250, 217,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 193, 20,   ┆ 150, 139,  ┆ 228, 228,  │
│            ┆          ┆           ┆           ┆   ┆       ┆ 211,…      ┆ …          ┆ …          │
│ MXN0001700 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 6     ┆ 99, 79,    ┆ 106, 89,   ┆ 300, 306,  │
│ 1          ┆          ┆           ┆       

### Nesting

We can also create a nested structure in polars by creating a new struct from existing columns. For example, we might want the latitude/longitude pair to be a struct.

In [26]:
udf.with_columns(pl.struct(["LATITUDE", "LONGITUDE"]).alias("LATLON")).drop(
    "LATITUDE", "LONGITUDE"
)

shape: (741, 9)
┌────────────┬───────────┬────────────┬──────┬───┬────────────┬────────────┬───────────┬───────────┐
│ ID         ┆ ELEVATION ┆ NAME       ┆ YEAR ┆ … ┆ PRCP       ┆ TMIN       ┆ TMAX      ┆ LATLON    │
│ ---        ┆ ---       ┆ ---        ┆ ---  ┆   ┆ ---        ┆ ---        ┆ ---       ┆ ---       │
│ str        ┆ f64       ┆ str        ┆ i64  ┆   ┆ str        ┆ str        ┆ str       ┆ struct[2] │
╞════════════╪═══════════╪════════════╪══════╪═══╪════════════╪════════════╪═══════════╪═══════════╡
│ MXN0001700 ┆ 1510.0    ┆ CUERNAVACA ┆ 2000 ┆ … ┆ 0, 0, 0,   ┆ 128, 117,  ┆ 267, 267, ┆ {18.9167, │
│ 4          ┆           ┆ DGE, MX    ┆      ┆   ┆ 0, 0, 0,   ┆ 128, 117,  ┆ 256, 250, ┆ -99.2333} │
│            ┆           ┆            ┆      ┆   ┆ 0, 0, 0,   ┆ 117, 117,  ┆ 250, 256, ┆           │
│            ┆           ┆            ┆      ┆   ┆ 0, …       ┆ …          ┆ …         ┆           │
│ MXN0001700 ┆ 1599.9    ┆ ATLATLAHUA ┆ 2009 ┆ … ┆ 0, 0, 0,   ┆ 156, 156,  ┆ 306, 306, ┆ {18.9333, │
│ 1          ┆           ┆ CAN, MX    ┆      ┆   ┆ 0, 0, 0,   ┆ 156, 156,  ┆ 300, 317, ┆ -98.9167} │
│            ┆           ┆            ┆      ┆   ┆ 0, 0, 0,   ┆ 117, 128,  ┆ 317, 317, ┆           │
│            ┆           ┆            ┆      ┆   ┆ 33,…       ┆ …          ┆ …         ┆           │
│ MXN0001700 ┆ 1857.8    ┆ EL RODEO,  ┆ 2002 ┆ … ┆ 0, 0, 0,   ┆ 150, 150,  ┆ 256, 256, ┆ {18.7667, │
│ 6          ┆           ┆ MX         ┆      ┆   ┆ 0, 0, 0,   ┆ 178, 156,  ┆ 289, 289, ┆ -99.3167} │
│            ┆           ┆            ┆      ┆   ┆ 15, 0, 0,  ┆ 167, 156,  ┆ 267, 278, ┆           │
│            ┆           ┆            ┆      ┆   ┆ 0,…        ┆ …          ┆ …         ┆           │
│ MXN0001700 ┆ 1599.9    ┆ ATLATLAHUA ┆ 2003 ┆ … ┆ 0, 0, 0,   ┆ 139, 128,  ┆ 339, 356, ┆ {18.9333, │
│ 1          ┆           ┆ CAN, MX    ┆      ┆   ┆ 0, 0, 0,   ┆ 117, 106,  ┆ 339, 350, ┆ -98.9167} │
│            ┆           ┆            ┆      ┆   ┆ 0, 0, 18,  ┆ 128, 128,  ┆ 356, 350, ┆           │
│            ┆           ┆            ┆      ┆   ┆ 0,…        ┆ …          ┆ …         ┆           │
│ MXN0001700 ┆ 941.8     ┆ HUAJINTLAN ┆ 2001 ┆ … ┆ 0, 0, 0,   ┆ 139, 128,  ┆ 300, 300, ┆ {18.6,-99 │
│ 7          ┆           ┆ , MX       ┆      ┆   ┆ 0, 0, 0,   ┆ 150, 117,  ┆ 289, 306, ┆ .4167}    │
│            ┆           ┆            ┆      ┆   ┆ 0, 0, 41,  ┆ 117, 117,  ┆ 317, 317, ┆           │
│            ┆           ┆            ┆      ┆   ┆ 0,…        ┆ …          ┆ …         ┆           │
│ …          ┆ …         ┆ …          ┆ …    ┆ … ┆ …          ┆ …          ┆ …         ┆ …         │
│ MXN0001700 ┆ 1302.7    ┆ CUAUTLA    ┆ 2009 ┆ … ┆ 28, 30, 0, ┆ 150, 156,  ┆ 250, 256, ┆ {18.8,-98 │
│ 3          ┆           ┆ SMN, MX    ┆      ┆   ┆ 0, 0, 0,   ┆ 128, 139,  ┆ 256, 256, ┆ .95}      │
│            ┆           ┆            ┆      ┆   ┆ 0, 0, 0,   ┆ 139, 128,  ┆ 256, 250, ┆           │
│            ┆           ┆            ┆      ┆   ┆ 0…         ┆ …          ┆ …         ┆           │
│ MXN0001700 ┆ 965.9     ┆ HUAUTLA,   ┆ 2007 ┆ … ┆ 0, 0, 0,   ┆ 139, 128,  ┆ 317, 317, ┆ {18.4333, │
│ 8          ┆           ┆ MX         ┆      ┆   ┆ 0, 0, 0,   ┆ 106, 128,  ┆ 328, 300, ┆ -99.0167} │
│            ┆           ┆            ┆      ┆   ┆ 0, 0, 0,   ┆ 106, 117,  ┆ 300, 289, ┆           │
│            ┆           ┆            ┆      ┆   ┆ 0, …       ┆ …          ┆ …         ┆           │
│ MXN0001700 ┆ 1599.9    ┆ ATLATLAHUA ┆ 2008 ┆ … ┆ 0, 117,    ┆ 139, 156,  ┆ 239, 217, ┆ {18.9333, │
│ 1          ┆           ┆ CAN, MX    ┆      ┆   ┆ 198, 41,   ┆ 128, 156,  ┆ 250, 217, ┆ -98.9167} │
│            ┆           ┆            ┆      ┆   ┆ 193, 20,   ┆ 150, 139,  ┆ 228, 228, ┆           │
│            ┆           ┆            ┆      ┆   ┆ 211,…      ┆ …          ┆ …         ┆           │
│ MXN0001700 ┆ 1599.9    ┆ ATLATLAHUA ┆ 2002 ┆ … ┆ 99, 79,    ┆ 106, 89,   ┆ 300, 306, ┆ {18.9333, │
│ 1          ┆           ┆ CAN, MX    ┆      

### Split and Explode

Another operation that can be useful, especially when we have lists of data in a column, is to explode that list into a bunch of new rows. In our data, the PRCP, TMIN,and TMAX columns are all strings so we need to first apply string operations to parse the string. Let's work on the PRCP column to begin.

#### Split

In [27]:
udf["PRCP"].str.split(",")

shape: (741,)
Series: 'PRCP' [list[str]]
[
	["0", " 0", … " 0"]
	["0", " 0", … " 216"]
	["0", " 0", … " 0"]
	["0", " 0", … " 30"]
	["0", " 0", … " 0"]
	…
	["28", " 30", … " 0"]
	["0", " 0", … " 0"]
	["0", " 117", … " 0"]
	["99", " 79", … " 102"]
	["0", " 0", … " 0"]
]

In [28]:
udf["PRCP"].str.split(",").cast(pl.List(pl.Int16))

shape: (741,)
Series: 'PRCP' [list[i16]]
[
	[0, null, … null]
	[0, null, … null]
	[0, null, … null]
	[0, null, … null]
	[0, null, … null]
	…
	[28, null, … null]
	[0, null, … null]
	[0, null, … null]
	[99, null, … null]
	[0, null, … null]
]

While we can cast a list of strings to a list of integers, this fails. The problem is that we have an extra space before each number. We can clean this up by changing our split separator to include a space or add an additional `strip_chars` call to string whitespace after the split. The second is a bit more robust, but it requires the `list.eval` expression that runs **element-wise** computations over the list.

In [29]:
udf["PRCP"].str.split(r", ").cast(pl.List(pl.Int16))

shape: (741,)
Series: 'PRCP' [list[i16]]
[
	[0, 0, … 0]
	[0, 0, … 216]
	[0, 0, … 0]
	[0, 0, … 30]
	[0, 0, … 0]
	…
	[28, 30, … 0]
	[0, 0, … 0]
	[0, 117, … 0]
	[99, 79, … 102]
	[0, 0, … 0]
]

In [30]:
udf["PRCP"].str.split(r",").list.eval(pl.element().str.strip_chars()).cast(
    pl.List(pl.Int16)
)

shape: (741,)
Series: 'PRCP' [list[i16]]
[
	[0, 0, … 0]
	[0, 0, … 216]
	[0, 0, … 0]
	[0, 0, … 30]
	[0, 0, … 0]
	…
	[28, 30, … 0]
	[0, 0, … 0]
	[0, 117, … 0]
	[99, 79, … 102]
	[0, 0, … 0]
]

##### Exercise

Convert all three columns (PRCP, TMIN, and TMAX).

##### Solution


Since polars allows references to columns to include multiple columns, we can write the code once for all three columns.

In [31]:
sdf = udf.with_columns(
    pl.col("PRCP", "TMIN", "TMAX")
    .str.split(r",")
    .list.eval(pl.element().str.strip_chars())
    .cast(pl.List(pl.Int16))
)

shape: (741, 10)
┌────────────┬──────────┬───────────┬───────────┬───┬───────┬────────────┬────────────┬────────────┐
│ ID         ┆ LATITUDE ┆ LONGITUDE ┆ ELEVATION ┆ … ┆ MONTH ┆ PRCP       ┆ TMIN       ┆ TMAX       │
│ ---        ┆ ---      ┆ ---       ┆ ---       ┆   ┆ ---   ┆ ---        ┆ ---        ┆ ---        │
│ str        ┆ f64      ┆ f64       ┆ f64       ┆   ┆ i64   ┆ list[i16]  ┆ list[i16]  ┆ list[i16]  │
╞════════════╪══════════╪═══════════╪═══════════╪═══╪═══════╪════════════╪════════════╪════════════╡
│ MXN0001700 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 2     ┆ [0, 0, …   ┆ [128, 117, ┆ [267, 267, │
│ 4          ┆          ┆           ┆           ┆   ┆       ┆ 0]         ┆ … 139]     ┆ … 328]     │
│ MXN0001700 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 5     ┆ [0, 0, …   ┆ [156, 156, ┆ [306, 306, │
│ 1          ┆          ┆           ┆           ┆   ┆       ┆ 216]       ┆ … 156]     ┆ … 278]     │
│ MXN0001700 ┆ 18.7667  ┆ -99.3167  ┆ 1857.8    ┆ … ┆ 3     ┆ [0, 0, …   ┆ [150, 150, ┆ [256, 256, │
│ 6          ┆          ┆           ┆           ┆   ┆       ┆ 0]         ┆ … 189]     ┆ … 306]     │
│ MXN0001700 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 5     ┆ [0, 0, …   ┆ [139, 128, ┆ [339, 356, │
│ 1          ┆          ┆           ┆           ┆   ┆       ┆ 30]        ┆ … 128]     ┆ … 328]     │
│ MXN0001700 ┆ 18.6     ┆ -99.4167  ┆ 941.8     ┆ … ┆ 1     ┆ [0, 0, …   ┆ [139, 128, ┆ [300, 300, │
│ 7          ┆          ┆           ┆           ┆   ┆       ┆ 0]         ┆ … 139]     ┆ … 350]     │
│ …          ┆ …        ┆ …         ┆ …         ┆ … ┆ …     ┆ …          ┆ …          ┆ …          │
│ MXN0001700 ┆ 18.8     ┆ -98.95    ┆ 1302.7    ┆ … ┆ 11    ┆ [28, 30, … ┆ [150, 156, ┆ [250, 256, │
│ 3          ┆          ┆           ┆           ┆   ┆       ┆ 0]         ┆ … 128]     ┆ … 256]     │
│ MXN0001700 ┆ 18.4333  ┆ -99.0167  ┆ 965.9     ┆ … ┆ 11    ┆ [0, 0, …   ┆ [139, 128, ┆ [317, 317, │
│ 8          ┆          ┆           ┆           ┆   ┆       ┆ 0]         ┆ … 117]     ┆ … 300]     │
│ MXN0001700 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 9     ┆ [0, 117, … ┆ [139, 156, ┆ [239, 217, │
│ 1          ┆          ┆           ┆           ┆   ┆       ┆ 0]         ┆ … 128]     ┆ … 250]     │
│ MXN0001700 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 6     ┆ [99, 79, … ┆ [106, 89,  ┆ [300, 306, │
│ 1          ┆          ┆           ┆           ┆   ┆       ┆ 102]       ┆ … 106]     ┆ … 289]     │
│ MXN0001700 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 4     ┆ [0, 0, …   ┆ [150, 139, ┆ [278, 317, │
│ 1          ┆          ┆           ┆           ┆   ┆       ┆ 0]         ┆ … 128]     ┆ … 378]     │
└────────────┴──────────┴───────────┴───────────┴───┴───────┴────────────┴────────────┴────────────┘

#### Explode

Now, we can run our `explode` operation which will take each element from the list columns and add a new row for each. If we pass all three columns at once, polars will put one entrty from each column into each new row.

In [32]:
sdf.explode("PRCP", "TMIN", "TMAX")

shape: (22_555, 10)
┌─────────────┬──────────┬───────────┬───────────┬───┬───────┬──────┬──────┬──────┐
│ ID          ┆ LATITUDE ┆ LONGITUDE ┆ ELEVATION ┆ … ┆ MONTH ┆ PRCP ┆ TMIN ┆ TMAX │
│ ---         ┆ ---      ┆ ---       ┆ ---       ┆   ┆ ---   ┆ ---  ┆ ---  ┆ ---  │
│ str         ┆ f64      ┆ f64       ┆ f64       ┆   ┆ i64   ┆ i16  ┆ i16  ┆ i16  │
╞═════════════╪══════════╪═══════════╪═══════════╪═══╪═══════╪══════╪══════╪══════╡
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 2     ┆ 0    ┆ 128  ┆ 267  │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 2     ┆ 0    ┆ 117  ┆ 267  │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 2     ┆ 0    ┆ 128  ┆ 256  │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 2     ┆ 0    ┆ 117  ┆ 250  │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 2     ┆ 0    ┆ 117  ┆ 250  │
│ …           ┆ …        ┆ …         ┆ …         ┆ … ┆ …     ┆ …    ┆ …    ┆ …    │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 4     ┆ 0    ┆ 139  ┆ 356  │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 4     ┆ 0    ┆ 150  ┆ 389  │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 4     ┆ 470  ┆ 139  ┆ 350  │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 4     ┆ 0    ┆ 150  ┆ 350  │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 4     ┆ 0    ┆ 128  ┆ 378  │
└─────────────┴──────────┴───────────┴───────────┴───┴───────┴──────┴──────┴──────┘

This looks pretty close to what we had for the tidy data above, except that we don't have the day of the month! While polars doesn't have the `enumerate` call from Python, it does have the ability to create a range of integers of the same size as a list. We will use `int_ranges` to create the days that should be paired with each entry. Since this function normally starts with zero and the first day of the month is one, we add one to the bounds of our int_ranges.

In [33]:
edf = sdf.with_columns(
    pl.int_ranges(1, pl.col("PRCP").list.len() + 1).alias("DAY")
).explode("PRCP", "TMIN", "TMAX", "DAY")

shape: (22_555, 11)
┌─────────────┬──────────┬───────────┬───────────┬───┬──────┬──────┬──────┬─────┐
│ ID          ┆ LATITUDE ┆ LONGITUDE ┆ ELEVATION ┆ … ┆ PRCP ┆ TMIN ┆ TMAX ┆ DAY │
│ ---         ┆ ---      ┆ ---       ┆ ---       ┆   ┆ ---  ┆ ---  ┆ ---  ┆ --- │
│ str         ┆ f64      ┆ f64       ┆ f64       ┆   ┆ i16  ┆ i16  ┆ i16  ┆ i64 │
╞═════════════╪══════════╪═══════════╪═══════════╪═══╪══════╪══════╪══════╪═════╡
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 0    ┆ 128  ┆ 267  ┆ 1   │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 0    ┆ 117  ┆ 267  ┆ 2   │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 0    ┆ 128  ┆ 256  ┆ 3   │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 0    ┆ 117  ┆ 250  ┆ 4   │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 0    ┆ 117  ┆ 250  ┆ 5   │
│ …           ┆ …        ┆ …         ┆ …         ┆ … ┆ …    ┆ …    ┆ …    ┆ …   │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 0    ┆ 139  ┆ 356  ┆ 26  │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 0    ┆ 150  ┆ 389  ┆ 27  │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 470  ┆ 139  ┆ 350  ┆ 28  │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 0    ┆ 150  ┆ 350  ┆ 29  │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 0    ┆ 128  ┆ 378  ┆ 30  │
└─────────────┴──────────┴───────────┴───────────┴───┴──────┴──────┴──────┴─────┘

##### Exercise

Using the exploded dataframe `edf`, create a new DATE column that puts the YEAR, MONTH, and DAY together into a single data. Drop the YEAR, MONTH, and DAY columns. Store this dataframe as `ddf`.

##### Solution

In [34]:
ddf = edf.with_columns(
    pl.date(pl.col("YEAR"), pl.col("MONTH"), pl.col("DAY")).alias("DATE")
).drop("YEAR", "MONTH", "DAY")

shape: (22_555, 9)
┌─────────────┬──────────┬───────────┬───────────┬───┬──────┬──────┬──────┬────────────┐
│ ID          ┆ LATITUDE ┆ LONGITUDE ┆ ELEVATION ┆ … ┆ PRCP ┆ TMIN ┆ TMAX ┆ DATE       │
│ ---         ┆ ---      ┆ ---       ┆ ---       ┆   ┆ ---  ┆ ---  ┆ ---  ┆ ---        │
│ str         ┆ f64      ┆ f64       ┆ f64       ┆   ┆ i16  ┆ i16  ┆ i16  ┆ date       │
╞═════════════╪══════════╪═══════════╪═══════════╪═══╪══════╪══════╪══════╪════════════╡
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 0    ┆ 128  ┆ 267  ┆ 2000-02-01 │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 0    ┆ 117  ┆ 267  ┆ 2000-02-02 │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 0    ┆ 128  ┆ 256  ┆ 2000-02-03 │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 0    ┆ 117  ┆ 250  ┆ 2000-02-04 │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 0    ┆ 117  ┆ 250  ┆ 2000-02-05 │
│ …           ┆ …        ┆ …         ┆ …         ┆ … ┆ …    ┆ …    ┆ …    ┆ …          │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 0    ┆ 139  ┆ 356  ┆ 2004-04-26 │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 0    ┆ 150  ┆ 389  ┆ 2004-04-27 │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 470  ┆ 139  ┆ 350  ┆ 2004-04-28 │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 0    ┆ 150  ┆ 350  ┆ 2004-04-29 │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 0    ┆ 128  ┆ 378  ┆ 2004-04-30 │
└─────────────┴──────────┴───────────┴───────────┴───┴──────┴──────┴──────┴────────────┘

### Normalization

You may have noticed that the station information seems to be the same for each unique `ID`. We may be able to normalize station information from the rest of the data. Let's check that the `ID` does determine the rest of the columns.

In [35]:
station_info = ddf.select("ID", "LATITUDE", "LONGITUDE", "ELEVATION", "NAME").unique()

shape: (7, 5)
┌─────────────┬──────────┬───────────┬───────────┬──────────────────────┐
│ ID          ┆ LATITUDE ┆ LONGITUDE ┆ ELEVATION ┆ NAME                 │
│ ---         ┆ ---      ┆ ---       ┆ ---       ┆ ---                  │
│ str         ┆ f64      ┆ f64       ┆ f64       ┆ str                  │
╞═════════════╪══════════╪═══════════╪═══════════╪══════════════════════╡
│ MXN00017003 ┆ 18.8     ┆ -98.95    ┆ 1302.7    ┆ CUAUTLA SMN, MX      │
│ MXN00017007 ┆ 18.6     ┆ -99.4167  ┆ 941.8     ┆ HUAJINTLAN, MX       │
│ MXN00017002 ┆ 18.9333  ┆ -99.2167  ┆ 1613.9    ┆ COLONIA EMPLEADO, MX │
│ MXN00017006 ┆ 18.7667  ┆ -99.3167  ┆ 1857.8    ┆ EL RODEO, MX         │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ CUERNAVACA DGE, MX   │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ ATLATLAHUACAN, MX    │
│ MXN00017008 ┆ 18.4333  ┆ -99.0167  ┆ 965.9     ┆ HUAUTLA, MX          │
└─────────────┴──────────┴───────────┴───────────┴──────────────────────┘

This looks good. We can use this to create two dataframes, one for station information and one for weather.

In [36]:
weather_info = ddf.select("ID", "DATE", "PRCP", "TMIN", "TMAX")

shape: (22_555, 5)
┌─────────────┬────────────┬──────┬──────┬──────┐
│ ID          ┆ DATE       ┆ PRCP ┆ TMIN ┆ TMAX │
│ ---         ┆ ---        ┆ ---  ┆ ---  ┆ ---  │
│ str         ┆ date       ┆ i16  ┆ i16  ┆ i16  │
╞═════════════╪════════════╪══════╪══════╪══════╡
│ MXN00017004 ┆ 2000-02-01 ┆ 0    ┆ 128  ┆ 267  │
│ MXN00017004 ┆ 2000-02-02 ┆ 0    ┆ 117  ┆ 267  │
│ MXN00017004 ┆ 2000-02-03 ┆ 0    ┆ 128  ┆ 256  │
│ MXN00017004 ┆ 2000-02-04 ┆ 0    ┆ 117  ┆ 250  │
│ MXN00017004 ┆ 2000-02-05 ┆ 0    ┆ 117  ┆ 250  │
│ …           ┆ …          ┆ …    ┆ …    ┆ …    │
│ MXN00017001 ┆ 2004-04-26 ┆ 0    ┆ 139  ┆ 356  │
│ MXN00017001 ┆ 2004-04-27 ┆ 0    ┆ 150  ┆ 389  │
│ MXN00017001 ┆ 2004-04-28 ┆ 470  ┆ 139  ┆ 350  │
│ MXN00017001 ┆ 2004-04-29 ┆ 0    ┆ 150  ┆ 350  │
│ MXN00017001 ┆ 2004-04-30 ┆ 0    ┆ 128  ┆ 378  │
└─────────────┴────────────┴──────┴──────┴──────┘

This normalization is common in databases, and we can see that fewer cells are required to represent the information. If we save them as csv files, we can see that the total space required decreases.

In [37]:
from pathlib import Path

names = ["all_info", "station_info", "weather_info"]

for write_df, name in zip([ddf, station_info, weather_info], names):
    write_df.write_csv(f"{name}.csv")

sz = {}
for name in names:
    p = Path(f"{name}.csv")
    print(name, p.stat().st_size)
    sz[name] = p.stat().st_size
    p.unlink()
print("Ratio:", (sz["station_info"] + sz["weather_info"]) / sz["all_info"])

all_info 1659616
station_info 407
weather_info 750034
Ratio: 0.4521774916607215


We use about half as much storage with csv files. However, if we store them as parquet files, the storage size doesn't change much at all. In fact, you may see that the full dataset requires **less** space that normalized dataframes. Because parquet uses compression techniques, it uses almost no space to repeat the same values over and over.

In [38]:
from pathlib import Path

for write_df, name in zip(
    [ddf.sort("ID"), station_info.sort("ID"), weather_info.sort("ID")], names
):
    write_df.write_parquet(f"{name}.parquet")

sz = {}
for name in names:
    p = Path(f"{name}.parquet")
    print(name, p.stat().st_size)
    sz[name] = p.stat().st_size
    p.unlink()
print("Ratio:", (sz["station_info"] + sz["weather_info"]) / sz["all_info"])

all_info 60304
station_info 2162
weather_info 58456
Ratio: 1.005206951446007


### Join

To understand the normalized dataset as a whole, we can join the tables together.

In [39]:
station_info.join(weather_info, on="ID", how="inner")

shape: (22_555, 9)
┌─────────────┬──────────┬───────────┬───────────┬───┬────────────┬──────┬──────┬──────┐
│ ID          ┆ LATITUDE ┆ LONGITUDE ┆ ELEVATION ┆ … ┆ DATE       ┆ PRCP ┆ TMIN ┆ TMAX │
│ ---         ┆ ---      ┆ ---       ┆ ---       ┆   ┆ ---        ┆ ---  ┆ ---  ┆ ---  │
│ str         ┆ f64      ┆ f64       ┆ f64       ┆   ┆ date       ┆ i16  ┆ i16  ┆ i16  │
╞═════════════╪══════════╪═══════════╪═══════════╪═══╪════════════╪══════╪══════╪══════╡
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 2000-02-01 ┆ 0    ┆ 128  ┆ 267  │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 2000-02-02 ┆ 0    ┆ 117  ┆ 267  │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 2000-02-03 ┆ 0    ┆ 128  ┆ 256  │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 2000-02-04 ┆ 0    ┆ 117  ┆ 250  │
│ MXN00017004 ┆ 18.9167  ┆ -99.2333  ┆ 1510.0    ┆ … ┆ 2000-02-05 ┆ 0    ┆ 117  ┆ 250  │
│ …           ┆ …        ┆ …         ┆ …         ┆ … ┆ …          ┆ …    ┆ …    ┆ …    │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 2004-04-26 ┆ 0    ┆ 139  ┆ 356  │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 2004-04-27 ┆ 0    ┆ 150  ┆ 389  │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 2004-04-28 ┆ 470  ┆ 139  ┆ 350  │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 2004-04-29 ┆ 0    ┆ 150  ┆ 350  │
│ MXN00017001 ┆ 18.9333  ┆ -98.9167  ┆ 1599.9    ┆ … ┆ 2004-04-30 ┆ 0    ┆ 128  ┆ 378  │
└─────────────┴──────────┴───────────┴───────────┴───┴────────────┴──────┴──────┴──────┘

A join has different strategies. Above, we used the default "inner" join, but you can also use "left", "right", and "full" (outer) joins in polars. In addition, polars provides an "anti" join which finds those rows on the left that have no match on the right.

## Final Exercise

Using our transformed data (`ddf`), transform this dataset so that we can compare the TMAX values between the seven different stations over ten days starting from 2004-04-01.